<a href="https://colab.research.google.com/github/yeray142/AIML_project/blob/master/notebooks/SVM_with_CODE_column.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# ML4AI | SVM with "CODE" column

> Result <br>
> **Log-Loss : 0.839775723576156**

### Set up for Project

#### Library

In [1]:
import pandas as pd
import numpy as np

!pip install -U pandas_profiling
import pandas_profiling as Profiling



Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [2]:
# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib as mpl

mpl.rc('axes', labelsize=14)
mpl.rc('xtick', labelsize=12)
mpl.rc('ytick', labelsize=12)

In [3]:
# Modeling
import sklearn
assert sklearn.__version__ >= "0.20"

from sklearn.model_selection import train_test_split,GridSearchCV,cross_val_score, KFold
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import RobustScaler

from sklearn.svm import SVC
from sklearn.metrics import log_loss

#### Data Load

In [4]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [5]:
df_train = pd.read_csv("/content/drive/MyDrive/ML4AI/cleaned_train.csv")
df_test = pd.read_csv("/content/drive/MyDrive/ML4AI/cleaned_test.csv")

## Data EDA

#### **Basic EDA**

In [6]:
df_train.head()

Unnamed: 0 gender car reality  child_num  income_total  \
0           0      F   N       N          0      202500.0   
1           1      F   N       Y          1      247500.0   
2           2      M   Y       Y          0      450000.0   
3           3      F   N       Y          0      202500.0   
4           4      F   Y       Y          0      157500.0   

            income_type                       edu_type     family_type  \
0  Commercial associate               Higher education         Married   
1  Commercial associate  Secondary / secondary special  Civil marriage   
2               Working               Higher education         Married   
3  Commercial associate  Secondary / secondary special         Married   
4         State servant               Higher education         Married   

            house_type  days_birth  days_employed  work_phone  home_phone  \
0  Municipal apartment       13899           4709           0           0   
1    House / apartment       11380           1540           0           0   
2    House / apartment       19087           4434           0           1   
3    House / apartment       15088           2092           0           1   
4    House / apartment       15037           2105           0           0   

   email   occup_type  family_size  begin_month  credit  \
0      0       No job          2.0            6     1.0   
1      1     Laborers          3.0            5     1.0   
2      0     Managers          2.0           22     2.0   
3      0  Sales staff          2.0           37     0.0   
4      0     Managers          2.0           26     2.0   

                                  CODE  
0  F-13899202500.0Commercial associate  
1  F-11380247500.0Commercial associate  
2               M-19087450000.0Working  
3  F-15088202500.0Commercial associate  
4         F-15037157500.0State servant

In [7]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24817 entries, 0 to 24816
Data columns (total 20 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Unnamed: 0     24817 non-null  int64  
 1   gender         24817 non-null  object 
 2   car            24817 non-null  object 
 3   reality        24817 non-null  object 
 4   child_num      24817 non-null  int64  
 5   income_total   24817 non-null  float64
 6   income_type    24817 non-null  object 
 7   edu_type       24817 non-null  object 
 8   family_type    24817 non-null  object 
 9   house_type     24817 non-null  object 
 10  days_birth     24817 non-null  int64  
 11  days_employed  24817 non-null  int64  
 12  work_phone     24817 non-null  int64  
 13  home_phone     24817 non-null  int64  
 14  email          24817 non-null  int64  
 15  occup_type     24817 non-null  object 
 16  family_size    24817 non-null  float64
 17  begin_month    24817 non-null  int64  
 18  credit

In [8]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 19 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   index          10000 non-null  int64  
 1   gender         10000 non-null  object 
 2   car            10000 non-null  object 
 3   reality        10000 non-null  object 
 4   child_num      10000 non-null  int64  
 5   income_total   10000 non-null  float64
 6   income_type    10000 non-null  object 
 7   edu_type       10000 non-null  object 
 8   family_type    10000 non-null  object 
 9   house_type     10000 non-null  object 
 10  days_birth     10000 non-null  int64  
 11  days_employed  10000 non-null  int64  
 12  work_phone     10000 non-null  int64  
 13  home_phone     10000 non-null  int64  
 14  email          10000 non-null  int64  
 15  occup_type     10000 non-null  object 
 16  family_size    10000 non-null  float64
 17  begin_month    10000 non-null  int64  
 18  CODE   

In [9]:
df_train.isna().sum()

Unnamed: 0       0
gender           0
car              0
reality          0
child_num        0
income_total     0
income_type      0
edu_type         0
family_type      0
house_type       0
days_birth       0
days_employed    0
work_phone       0
home_phone       0
email            0
occup_type       0
family_size      0
begin_month      0
credit           0
CODE             0
dtype: int64

In [10]:
df_test.isna().sum()

index            0
gender           0
car              0
reality          0
child_num        0
income_total     0
income_type      0
edu_type         0
family_type      0
house_type       0
days_birth       0
days_employed    0
work_phone       0
home_phone       0
email            0
occup_type       0
family_size      0
begin_month      0
CODE             0
dtype: int64

In [11]:
df_train['occup_type'].value_counts()

No job                   7612
Laborers                 4254
Core staff               2502
Sales staff              2381
Managers                 2024
Drivers                  1487
High skill tech staff     983
Accountants               838
Medicine staff            812
Cooking staff             433
Security staff            399
Cleaning staff            384
Private service staff     226
Waiters/barmen staff      118
Low-skill Laborers        115
Secretaries                94
Realty agents              58
HR staff                   57
IT staff                   40
Name: occup_type, dtype: int64

DAYS_BIRTH, DAYS_EMPLOYED, BIGIN_MONTH is calculated by days from data collect. <br> 
$\Rightarrow$ If days_birth is 1, then it means that the observation is borned one day before data collecting has processed. <br>
$\Rightarrow$ So Observations that has positive days_employeed is replaced "No Job" <br>
$\Rightarrow$ Then we replace negative sign to positive sign, Under the assumption that there's mistake in sign enter. 

In [12]:
var_lst = ['days_birth', 'begin_month', 'days_employed']
for var in var_lst:
    df_train[var]=np.abs(df_train[var])
    df_test[var] = np.abs(df_test[var])

In [13]:
df_train.describe()

Unnamed: 0     child_num  income_total    days_birth  days_employed  \
count  24817.000000  24817.000000  2.481700e+04  24817.000000   24817.000000   
mean   12408.000000      0.430874  1.868744e+05  15951.287625    2198.272112   
std     7164.195151      0.750609  1.008656e+05   4205.102462    2371.033103   
min        0.000000      0.000000  2.700000e+04   7705.000000       0.000000   
25%     6204.000000      0.000000  1.215000e+05  12443.000000     407.000000   
50%    12408.000000      0.000000  1.575000e+05  15536.000000    1539.000000   
75%    18612.000000      1.000000  2.250000e+05  19428.000000    3153.000000   
max    24816.000000     19.000000  1.575000e+06  25152.000000   15713.000000   

         work_phone    home_phone         email   family_size   begin_month  \
count  24817.000000  24817.000000  24817.000000  24817.000000  24817.000000   
mean       0.225249      0.294274      0.091510      2.199057     26.054318   
std        0.417754      0.455725      0.288339      0.919132     16.532853   
min        0.000000      0.000000      0.000000      1.000000      0.000000   
25%        0.000000      0.000000      0.000000      2.000000     12.000000   
50%        0.000000      0.000000      0.000000      2.000000     24.000000   
75%        0.000000      1.000000      0.000000      3.000000     39.000000   
max        1.000000      1.000000      1.000000     20.000000     60.000000   

             credit  
count  24817.000000  
mean       1.514325  
std        0.704571  
min        0.000000  
25%        1.000000  
50%        2.000000  
75%        2.000000  
max        2.000000

#### **Detail EDA for using Profiling**

In [14]:
Profiling.ProfileReport(df_train)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

> **Result of more detailed EDA by using profiling**
- Data has 11 categorical features, 2 Boolean features, 6 numeric features.
- For "FlAG-MOBIL", there's only one value '1'. <br>
⇒ As everyone has mobile, so its importance to predict credit doesn't exist. Then we need to remove that.
- There's data imblancing for some features like "house_type","child_num" etc.
- There's strong correlattions between "income_type" and "Days_Employeed", "family_size" and "child_num".


## Data modeling

### Data Preprocessing for construct model

1) Encoding of categorical features

In [15]:
cat_cols = [x for x in df_train.columns if df_train[x].dtype == 'object']
float_cols = [x for x in df_train.columns.drop('credit') if df_train[x].dtype == 'float64']
num_cols = [x for x in df_train.columns if x not in cat_cols + ['credit']]
feature_cols = num_cols + cat_cols

In [16]:
cat_cols

['gender',
 'car',
 'reality',
 'income_type',
 'edu_type',
 'family_type',
 'house_type',
 'occup_type',
 'CODE']

In [17]:
float_cols

['income_total', 'family_size']

In [18]:
df_test.head()

index gender car reality  child_num  income_total           income_type  \
0  26457      M   Y       N          0      112500.0             Pensioner   
1  26458      F   N       Y          0      135000.0         State servant   
2  26459      F   N       Y          0       69372.0               Working   
3  26460      M   Y       N          0      112500.0  Commercial associate   
4  26461      F   Y       Y          0      225000.0         State servant   

                        edu_type     family_type         house_type  \
0  Secondary / secondary special  Civil marriage  House / apartment   
1               Higher education         Married  House / apartment   
2  Secondary / secondary special         Married  House / apartment   
3  Secondary / secondary special         Married  House / apartment   
4               Higher education         Married  House / apartment   

   days_birth  days_employed  work_phone  home_phone  email  occup_type  \
0       21990              0           0           1      0      No job   
1       18964           8671           0           1      0  Core staff   
2       15887            217           1           1      0    Laborers   
3       19270           2531           1           0      0     Drivers   
4       17822           9385           1           0      0    Managers   

   family_size  begin_month                                 CODE  
0          2.0           60             M-21990112500.0Pensioner  
1          2.0           36         F-18964135000.0State servant  
2          2.0           40                F-1588769372.0Working  
3          2.0           41  M-19270112500.0Commercial associate  
4          2.0            8         F-17822225000.0State servant

In [19]:
Encoder = LabelEncoder()


for i in cat_cols:
    df_train[i] = Encoder.fit_transform(df_train[i].astype(str))

for i in float_cols:
    df_train[i] = df_train[i].astype('int')

for label in np.unique(df_test.columns):
    if label not in Encoder.classes_: # unseen label 데이터인 경우( )
        Encoder.classes_ = np.append(Encoder.classes_, label) # 미처리 시 ValueError발생

for i in cat_cols:
    df_test[i] = Encoder.fit_transform(df_test[i].astype(str))

for i in float_cols:
    df_test[i] = df_test[i].astype('int')

In [20]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 19 columns):
 #   Column         Non-Null Count  Dtype
---  ------         --------------  -----
 0   index          10000 non-null  int64
 1   gender         10000 non-null  int64
 2   car            10000 non-null  int64
 3   reality        10000 non-null  int64
 4   child_num      10000 non-null  int64
 5   income_total   10000 non-null  int64
 6   income_type    10000 non-null  int64
 7   edu_type       10000 non-null  int64
 8   family_type    10000 non-null  int64
 9   house_type     10000 non-null  int64
 10  days_birth     10000 non-null  int64
 11  days_employed  10000 non-null  int64
 12  work_phone     10000 non-null  int64
 13  home_phone     10000 non-null  int64
 14  email          10000 non-null  int64
 15  occup_type     10000 non-null  int64
 16  family_size    10000 non-null  int64
 17  begin_month    10000 non-null  int64
 18  CODE           10000 non-null  int64
dtypes: in

3) Data Split ⇒ We need to split with stratified split

In [21]:
X_train, X_val, y_train, y_val = train_test_split(df_train.loc[:,df_train.columns != 'credit'], df_train['credit'], test_size = 0.2)

In [22]:
X_train.head()

Unnamed: 0  gender  car  reality  child_num  income_total  income_type  \
9761         9761       1    0        0          1        360000            4   
22538       22538       1    1        1          2        225000            0   
10159       10159       0    0        0          0        202500            1   
9403         9403       1    1        0          0        315000            0   
6810         6810       1    1        1          0        180000            0   

       edu_type  family_type  house_type  days_birth  days_employed  \
9761          1            1           1       11112            469   
22538         4            1           1       15290           1405   
10159         4            4           2       21010              0   
9403          4            1           1       18214           5210   
6810          1            1           1        9925           1023   

       work_phone  home_phone  email  occup_type  family_size  begin_month  \
9761            1           1      0          10            3           37   
22538           0           0      0           8            4            3   
10159           0           1      1          12            1           22   
9403            1           1      0           8            2           23   
6810            0           0      0           8            2           43   

       CODE  
9761   5992  
22538  7066  
10159  4318  
9403   7660  
6810   8667

2) Feature scaling

In [23]:
from sklearn.preprocessing import RobustScaler

scaler = RobustScaler()

scaler.fit(X_train)
X_train = scaler.transform(X_train)
X_val = scaler.transform(X_val)
df_test = scaler.transform(df_test)


/usr/local/lib/python3.8/dist-packages/sklearn/base.py:493: FutureWarning: The feature names should match those that were passed during fit. Starting version 1.2, an error will be raised.
Feature names unseen at fit time:
- index
Feature names seen at fit time, yet now missing:
- Unnamed: 0

  warnings.warn(message, FutureWarning)


### Modeling

- 1) SVC : SVM(Support vector machine) for classifier

(1) Grid Search for Hyper-parameter tuning

In [24]:
param_grid = [
    {'kernel': ['linear'], 'C': [1.0, 5.0, 10.0]},
    {'kernel': ['rbf'], 'C': [1.0, 5.0, 10.],
                        'gamma': [0.01, 0.05, 0.1, 0.5, 1.0]},
]

In [25]:
from sklearn.svm import SVC
 
svm_model = SVC()


In [26]:
grid_search = GridSearchCV(svm_model, param_grid, cv=5, scoring='accuracy', verbose=2)
grid_search.fit(X_train, y_train)

Fitting 5 folds for each of 18 candidates, totalling 90 fits
[CV] END ...............................C=1.0, kernel=linear; total time=   9.9s
[CV] END ...............................C=1.0, kernel=linear; total time=   9.0s
[CV] END ...............................C=1.0, kernel=linear; total time=   8.8s
[CV] END ...............................C=1.0, kernel=linear; total time=   8.9s
[CV] END ...............................C=1.0, kernel=linear; total time=   9.0s
[CV] END ...............................C=5.0, kernel=linear; total time=  15.8s
[CV] END ...............................C=5.0, kernel=linear; total time=  16.0s
[CV] END ...............................C=5.0, kernel=linear; total time=  17.7s
[CV] END ...............................C=5.0, kernel=linear; total time=  16.0s
[CV] END ...............................C=5.0, kernel=linear; total time=  15.7s
[CV] END ..............................C=10.0, kernel=linear; total time=  24.0s
[CV] END ..............................C=10.0, k

GridSearchCV(cv=5, estimator=SVC(),
             param_grid=[{'C': [1.0, 5.0, 10.0], 'kernel': ['linear']},
                         {'C': [1.0, 5.0, 10.0],
                          'gamma': [0.01, 0.05, 0.1, 0.5, 1.0],
                          'kernel': ['rbf']}],
             scoring='accuracy', verbose=2)

In [28]:
grid_search.best_params_

{'C': 10.0, 'gamma': 0.1, 'kernel': 'rbf'}

In [29]:
from sklearn.svm import SVC
 
svm_model_tuned = SVC(kernel='rbf', C=10.0, gamma=0.1,probability=True,random_state = 2022,class_weight = 'balanced')
 
svm_model_tuned.fit(X_train, y_train)

SVC(C=10.0, class_weight='balanced', gamma=0.1, probability=True,
    random_state=2022)

In [30]:
y_pred = svm_model_tuned.predict_proba(X_val)

In [31]:
logloss=log_loss(y_val,y_pred)
logloss

0.839775723576156

In [32]:
Y_pred_grid = svm_model_tuned.predict_proba(df_test)

- The result of SVM with grid search has 0.8397757235  

(2) K-Fold for Hyper-parameter tuning

In [33]:
p = {"kernel" : "rbf",
     "C": 10.0,
     'gamma':0.1, 
     'probability' : True,
     'random_state' : 42,
     'class_weight' : 'balanced'
  }

In [34]:
X = df_train.drop("credit", axis=1)
y = df_train["credit"]
X_test = df_test.copy()

In [35]:
from sklearn.model_selection import StratifiedKFold

def stratified_kfold_svc(p, n_fold, X, y, X_test):
    # Declaring Stratified K-Fold:
    folds = StratifiedKFold(n_splits=n_fold, shuffle=True, random_state=42)
    splits = folds.split(X, y)
    
    # Initializing arrays:
    svc_oof = np.zeros((X.shape[0], 3))
    svc_preds = np.zeros((X_test.shape[0], 3))

    # Main loop:
    for fold, (train_idx, valid_idx) in enumerate(splits):
        print(f"============ Fold {fold} ============")
        
        X_train, X_valid = X.iloc[train_idx], X.iloc[valid_idx]
        y_train, y_valid = y.iloc[train_idx], y.iloc[valid_idx]
        
        # Model fit:
        model = SVC(**p)
        model.fit(X_train, y_train)

        svc_oof[valid_idx] = model.predict_proba(X_valid) # Infers the class probability of train dataset
        svc_preds += model.predict_proba(X_test) / n_fold # Infers the class probability of test dataset
        print(f"Log Loss Score: {log_loss(y_valid, svc_oof[valid_idx]):.5f}")

    log_score = log_loss(y, svc_oof)
    print(f"\nLog Loss Score: {log_score:.5f}")

    return svc_oof, svc_preds

In [36]:
svc_oof, svc_preds = stratified_kfold_svc(p, 10, X, y, X_test)

============ Fold 0 ============


/usr/local/lib/python3.8/dist-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but SVC was fitted with feature names
  warnings.warn(


Log Loss Score: 0.88736
============ Fold 1 ============


/usr/local/lib/python3.8/dist-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but SVC was fitted with feature names
  warnings.warn(


Log Loss Score: 0.88736
============ Fold 2 ============


...

Log Loss Score: 0.88720
============ Fold 8 ============


/usr/local/lib/python3.8/dist-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but SVC was fitted with feature names
  warnings.warn(


Log Loss Score: 0.88713
============ Fold 9 ============


/usr/local/lib/python3.8/dist-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but SVC was fitted with feature names
  warnings.warn(


Log Loss Score: 0.88716

Log Loss Score: 0.88717


-> This code for k-fold validation takes sooooo long time. So I need to re-write the codes.

The Result of SVM with K-fold has 

In [37]:
Y_pred_kfold = svc_preds

In [41]:
submission_grid = pd.read_csv("/content/drive/MyDrive/ML4AI/sample_submission.csv")
submission_grid.set_index("index", inplace=True)
submission_grid[:] = Y_pred_grid
submission_grid.head()

0         1         2
index                              
26457  0.188010  0.113559  0.698431
26458  0.268237  0.145848  0.585915
26459  0.224922  0.305211  0.469867
26460  0.141809  0.198776  0.659415
26461  0.123693  0.285049  0.591258

In [42]:
submission_kfold = pd.read_csv("/content/drive/MyDrive/ML4AI/sample_submission.csv")
submission_kfold.set_index("index", inplace=True)
submission_kfold[:] = Y_pred_kfold
submission_kfold.head()

0         1         2
index                              
26457  0.124058  0.238457  0.637485
26458  0.124058  0.238457  0.637485
26459  0.124058  0.238457  0.637485
26460  0.124058  0.238457  0.637485
26461  0.124058  0.238457  0.637485

In [43]:
submission_grid.to_csv('submission_grid.csv')
submission_kfold.to_csv('submission_kfold.csv')